In [17]:
%load_ext autoreload
%autoreload 2

import os

import os
import sys

module_path = os.path.abspath(os.path.join('..'))
if module_path not in sys.path:
    sys.path.append(module_path)

import pandas as pd
import geopandas as gpd
import osmnx as ox
import networkx as nx
import folium
from shapely.geometry import LineString
from shapely import wkt
import numpy as np
import swifter
from generator.preprocess import *
from generator.preprocess import remove_outlier_trajectories
from generator.road_network import RoadNetwork
import glob
from tqdm import tqdm
import torch
import seaborn as sns

The autoreload extension is already loaded. To reload it, use:
  %reload_ext autoreload


In [27]:
"""
 Generate osmnx network from csv
"""

df = pd.read_csv("../datasets/trajectories/hanover/temporal/hannover_streetgraph.csv")
df["geometry"] = df["geometry"].swifter.apply(wkt.loads)
gdf = gpd.GeoDataFrame(df, geometry="geometry")
gdf["coords"] = gdf["geometry"].swifter.apply(lambda x: list(x.coords))

Pandas Apply:   0%|          | 0/8620 [00:00<?, ?it/s]

Pandas Apply:   0%|          | 0/8620 [00:00<?, ?it/s]

In [9]:
gdf.shape

(8620, 12)

In [6]:
gdf = ox.io._stringify_nonnumeric_cols(gdf)
gdf["fid"] = np.arange(0, gdf.shape[0], dtype="int")  # id for each edge
gdf.to_file("../osm_data/hanover_temp" + "/edges.shp", encoding="utf-8")

In [4]:
G = nx.from_pandas_edgelist(gdf, "source", "target", True, nx.MultiDiGraph)
sG = [G.subgraph(c) for c in sorted(nx.weakly_connected_components(G), key=len, reverse=True)][0]
sdf = nx.to_pandas_edgelist(sG)
sdf["coords"] = sdf["geometry"].swifter.apply(lambda x: list(x.coords))
sdf.to_csv("../datasets/trajectories/hanover/temporal/hannover_streetgraph.csv")

Pandas Apply:   0%|          | 0/8620 [00:00<?, ?it/s]

In [25]:
gdf = gpd.GeoDataFrame(network.gdf_edges, geometry="geometry")
gdf["coords"] = gdf["geometry"].swifter.apply(lambda x: list(x.coords))

Pandas Apply:   0%|          | 0/1366 [00:00<?, ?it/s]

In [28]:
# Folium Heat Map
from folium import plugins
from folium.plugins import HeatMap
from collections import defaultdict
import branca.colormap
colors = sns.color_palette().as_hex()
print(colors)
m = folium.Map(location=[52.37052, 9.73322],
                    zoom_start = 8, width="50%", height="50%")

coords = gdf.loc[:, "coords"].values

for line in coords:
    data = [(c[1], c[0]) for c in line]
    folium.PolyLine(data, color=colors[0], weight=2.5, opacity=0.8).add_to(m)

# coords = gdf["coords"].values
# for line in coords:
#     data = [(c[1], c[0]) for c in line]
#     folium.PolyLine(data, color="green", weight=2.5, opacity=0.8).add_to(m)

# Display the map
#map_porto.save("heatmap_gps_points_porto.html")
m

['#1f77b4', '#ff7f0e', '#2ca02c', '#d62728', '#9467bd', '#8c564b', '#e377c2', '#7f7f7f', '#bcbd22', '#17becf']


In [5]:
network = RoadNetwork()
# network.load_hanover_temporal(path="../datasets/trajectories/hanover/temporal/hannover_streetgraph.csv")
# network = network.subsample_graph(ratio=0.4)
network.load_edges("../osm_data/hanover_temp_small_graph/")

In [24]:
network.gdf_edges

Unnamed_ 0                                 gm_id      id  \
u     v     key                                                             
87037 93516 0          7627  087c80ab-a270-0b4f-417f-7c08f1a24f0b  145195   
15090 8141  0          1327  087c7fd0-a698-0b4f-a183-7c082da54f0b  113275   
14807 87037 0          1295  087c8386-a21e-0b4f-ab80-7c0870a24f0b   88966   
84375 42388 0          7378  087c82c6-7171-0b4f-fe82-7c08ed714f0b  103616   
42388 84375 0          3678  087c82fe-71ed-0b4f-c682-7c0871714f0b  152482   
...                     ...                                   ...     ...   
70598 35872 0          6259  087cb9e9-ede3-0b4e-79ba-7c0888f04e0b  138998   
35872 70598 0          3139  087cba79-f088-0b4e-e9b9-7c08e3ed4e0b  101489   
23242 23243 0          2031  087cba26-e65f-0b4e-9dba-7c08f8e54e0b   12910   
65885 86082 0          5802  087cbd2b-e315-0b4e-25ba-7c08d3e54e0b  118748   
23243 75550 0          2032  087cba9d-e5f8-0b4e-34be-7c08c3e24e0b  168947   

                  fid  speed_limi  \
u     v     key                     
87037 93516 0       0        70.0   
15090 8141  0       1        70.0   
14807 87037 0       2        70.0   
84375 42388 0       3        50.0   
42388 84375 0       4        50.0   
...               ...         ...   
70598 35872 0    1361        50.0   
35872 70598 0    1362        50.0   
23242 23243 0    1363        50.0   
65885 86082 0    1364        50.0   
23243 75550 0    1365        50.0   

                                                            coords  \
u     v     key                                                      
87037 93516 0    [(9.768303900000001, 52.3771314), (9.7683449, ...   
15090 8141  0    [(9.769368, 52.3769124), (9.7693426, 52.376976...   
14807 87037 0    [(9.768221500000001, 52.377861900000006), (9.7...   
84375 42388 0    [(9.755761300000001, 52.37767), (9.75588470000...   
42388 84375 0    [(9.755884700000001, 52.3777258), (9.755761300...   
...                                                            ...   
70598 35872 0    [(9.722083000000001, 52.3917851), (9.722583700...   
35872 70598 0    [(9.7227599, 52.391929100000006), (9.7226905, ...   
23242 23243 0    [(9.7201593, 52.3918455), (9.720055700000001, ...   
65885 86082 0     [(9.719317, 52.3926187), (9.720019, 52.3918453)]   
23243 75550 0    [(9.720055700000001, 52.3919646), (9.719745900...   

                     length  \
u     v     key               
87037 93516 0     41.274658   
15090 8141  0    111.691132   
14807 87037 0     83.502800   
84375 42388 0     10.424039   
42388 84375 0     10.424039   
...                     ...   
70598 35872 0     48.909206   
35872 70598 0     48.909206   
23242 23243 0     14.993560   
65885 86082 0     98.309891   
23243 75550 0    116.397346   

                                                           osm_ids    highway  \
u     v     key                                                                 
87037 93516 0                    '{2696835589,551501215,25753559}'   tertiary   
15090 8141  0    '{25753561,1022695779,551501355,260557584,1022...   tertiary   
14807 87037 0       '{3584276959,2628669590,551501213,2696835589}'   tertiary   
84375 42388 0                              '{654072236,148181777}'   tertiary   
42388 84375 0                              '{148181777,654072236}'   tertiary   
...                                                            ...        ...   
70598 35872 0      '{1619565065,1678001655,6340847835,1226798305}'  secondary   
35872 70598 0      '{1226798305,6340847835,1678001655,1619565065}'  secondary   
23242 23243 0                             '{1484622525,628872258}'  secondary   
65885 86082 0                            '{6221488101,6221488100}'  secondary   
23243 75550 0                      '{628872258,61094001,80191376}'  secondary   

                 highway_en                                           geometry  
u     v     key                                                                 
87

In [12]:
gdf_edges = ox.io._stringify_nonnumeric_cols(network.gdf_edges)
gdf_edges["fid"] = np.arange(
    0, gdf_edges.shape[0], dtype="int"
)  # id for each edge

gdf_edges.to_file("../osm_data/hanover_temp_small_graph/" + "/edges.shp", encoding="utf-8")

In [3]:
# create dataframe for road segment mapping
df = pd.read_csv("../datasets/trajectories/hanover/hannover_inrix.csv")
rows = []
for _, g in tqdm(df.groupby("id")):
    if g.shape[0] < 5:
        continue
    traj = g[["longitude", "latitude", "time"]].copy()
    traj.loc[:, "time"] = pd.to_datetime(traj["time"], infer_datetime_format=True).dt.floor('s')
    traj.loc[:, "time"] = traj["time"].values.astype(np.int64) // 10 ** 9
    
    data = traj.to_numpy()
    time = data[1:, 2] - data[0, 2]
    time = np.insert(time, 0, 0)
    seq = LineString(data[:, :2])
    assert len(list(seq.coords)) == time.shape[0]
    rows.append((seq, time.astype(int).tolist(), traj.iloc[0, 2], traj.iloc[-1, 2]))

processed_df = pd.DataFrame(rows, columns=["POLYLINE", "timestamp", "start_stamp", "end_stamp"])
processed_df

100%|██████████| 77188/77188 [03:44<00:00, 343.60it/s]


POLYLINE  \
0      LINESTRING (9.8288 52.3326, 9.819705 52.331356...   
1      LINESTRING (9.6472 52.2823, 9.643848 52.283978...   
2      LINESTRING (9.7376 52.5465, 9.72797 52.541855,...   
3      LINESTRING (9.7119 52.343, 9.716048 52.344969,...   
4      LINESTRING (9.7585 52.3363, 9.762929 52.34235,...   
...                                                  ...   
73924  LINESTRING (10.0369 53.3593, 10.037012 53.3582...   
73925  LINESTRING (9.7278 52.3654, 9.727219 52.365731...   
73926  LINESTRING (9.8726 52.9458, 9.718267 52.63466,...   
73927  LINESTRING (9.738963 52.382663, 9.738996 52.38...   
73928  LINESTRING (9.7822 52.4016, 9.782285 52.401667...   

                                               timestamp  start_stamp  \
0      [0, 80, 424, 535, 613, 1094, 1171, 1453, 1528,...   1565974403   
1      [0, 30, 60, 90, 120, 172, 202, 232, 262, 292, ...   1567075203   
2                      [0, 138, 300, 485, 668, 801, 882]   1566184436   
3        [0, 90, 180, 229, 319, 409, 492, 582, 672, 762]   1568621637   
4      [0, 79, 141, 224, 377, 453, 580, 685, 763, 881...   1566671810   
...                                                  ...          ...   
73924  [0, 5, 8, 14, 15, 19, 25, 28, 30, 34, 39, 44, ...   1569563606   
73925  [0, 5, 8, 16, 19, 20, 25, 29, 35, 40, 46, 49, ...   1575029942   
73926  [0, 599, 703, 718, 733, 748, 763, 778, 1295, 1...   1573224957   
73927  [0, 5, 10, 15, 20, 25, 30, 35, 45, 50, 55, 60,...   1574319815   
73928  [0, 8, 15, 30, 45, 60, 75, 90, 105, 120, 135, ...   1566152132   

        end_stamp  
0      1565982018  
1      1567075868  
2      1566185318  
3      1568622399  
4      1566673656  
...           ...  
73924  1569569649  
73925  1575031187  
73926  1573226965  
73927  1574320945  
73928  1566159550  

[73929 rows x 4 columns]

In [4]:
from shapely.geometry import LineString, box

df = processed_df.copy()
city_bounds = network.bounds_edges
# df_clipped = clip_trajectories(processed_df.copy(), city_bounds, polyline_convert=True)
# df_clipped = filter_min_points(processed_df.copy(), 5)
bbox = box(*city_bounds)
gdf = gpd.GeoDataFrame(df, crs="epsg:4326", geometry="POLYLINE")

clipped = gpd.clip(gdf, bbox, keep_geom_type=True)

In [5]:
clipped

POLYLINE  \
18565  LINESTRING (9.75970 52.39390, 9.76275 52.39302...   
6157   LINESTRING (9.76487 52.39422, 9.76529 52.39394...   
17570  LINESTRING (9.73850 52.36750, 9.74263 52.36805...   
64850  LINESTRING (9.78670 52.37300, 9.78676 52.37309...   
71863  LINESTRING (9.77810 52.37480, 9.77962 52.37772...   
...                                                  ...   
22226  LINESTRING (9.78807 52.39100, 9.78791 52.39086...   
42293  LINESTRING (9.78807 52.39112, 9.78763 52.39080...   
13294  LINESTRING (9.71977 52.37843, 9.72248 52.37824...   
52286  LINESTRING (9.78131 52.36431, 9.78124 52.36443...   
54650  LINESTRING (9.76860 52.37600, 9.76838 52.37610...   

                                               timestamp  start_stamp  \
18565  [0, 120, 241, 362, 483, 603, 724, 968, 1089, 1...   1573818302   
6157   [0, 30, 94, 124, 154, 184, 214, 277, 307, 337,...   1574525822   
17570  [0, 115, 205, 295, 385, 475, 565, 655, 766, 85...   1569071883   
64850  [0, 15, 30, 45, 60, 75, 90, 92, 97, 103, 105, ...   1566574550   
71863  [0, 15, 30, 45, 60, 75, 90, 105, 120, 135, 150...   1567163528   
...                                                  ...          ...   
22226  [0, 2, 5, 10, 15, 17, 20, 24, 29, 33, 34, 39, ...   1569062275   
42293  [0, 14, 30, 46, 60, 75, 90, 104, 120, 135, 150...   1568776466   
13294  [0, 30, 60, 90, 120, 150, 207, 237, 267, 297, ...   1573410514   
52286  [0, 5, 7, 9, 24, 39, 54, 69, 84, 99, 114, 129,...   1573662945   
54650  [0, 2, 3, 13, 28, 43, 54, 58, 74, 89, 103, 119...   1567093909   

        end_stamp  
18565  1573824822  
6157   1574533547  
17570  1569079309  
64850  1566583944  
71863  1567169273  
...           ...  
22226  1569075970  
42293  1568790746  
13294  1573424938  
52286  1573677039  
54650  1567105126  

[21223 rows x 4 columns]

In [6]:
print(clipped.loc[0, "POLYLINE"])
print(processed_df.loc[0, "POLYLINE"])

#print(processed_df.loc[0, "POLYLINE"].contains(clipped.loc[0, "POLYLINE"]))

LINESTRING (9.78807326 52.390116491206484, 9.787736 52.390743, 9.78807326 52.390903056677054)
LINESTRING (9.8288 52.3326, 9.819705 52.331356, 9.787736 52.390743, 9.824655 52.408264, 9.850968 52.412861, 9.60824 52.422359, 9.569406 52.42263, 9.542397 52.42115, 9.508204 52.408611, 9.466822 52.381687, 9.435784 52.361549, 9.399967 52.328964, 9.372162 52.30423, 9.339224 52.277271, 9.322924 52.269669, 9.316408 52.265495, 9.313453 52.262424, 9.311065 52.259903, 9.30757 52.257214, 9.302485 52.254589, 9.297933 52.252476, 9.294051 52.250629, 9.289948 52.248016, 9.256525 52.233921, 9.200723 52.220062, 9.16455 52.216946, 9.106794 52.221832, 9.06195 52.220818, 9.003625 52.219688, 8.956563 52.215717, 8.882984 52.211132, 8.845288 52.206764, 8.80543 52.234589, 8.728555 52.206097, 8.650899 52.187443, 8.612735 52.178822, 8.608962 52.179413, 8.58045 52.188202, 8.532821 52.194088, 8.484649 52.195026, 8.421346 52.198208, 8.38777 52.19701, 8.370899 52.19566, 8.324356 52.194012, 8.24332 52.216385, 8.148149 52

In [7]:
def strictly_increasing(L):
    return all(x+20>=y for x, y in zip(L, L[1:]))


def correct_timestamps(traj, orig_trajs, orig_ts):
    corrected_ts = []
    corrected_traj = []
    idxs = []
    found = False
    for i, g1 in enumerate(traj):
        ridx = 0
        for j, g2 in enumerate(orig_trajs[ridx:]):
            if g1 == g2:
                found = True
                corrected_ts.append(orig_ts[j])
                corrected_traj.append(g1)
                idxs.append(j)
                ridx = j+1
                break
            # if found:
            #     break

    assert len(corrected_traj) == len(corrected_ts)
    # assert strictly_increasing(idxs), (idxs)
    
    return corrected_traj, (np.array(corrected_ts) - corrected_ts[0]).astype(int).tolist()


rows = []
i = 0
orig_polies, orig_ts = processed_df.POLYLINE, processed_df.timestamp
for i, r in tqdm(clipped.iterrows()):
    op = list(orig_polies.loc[r.name].coords)
    ot = orig_ts.loc[r.name]
    if type(r.POLYLINE) == LineString:
        traj = list(r.POLYLINE.coords)
        if len(traj) < 5:
            continue
        ctraj, cts = correct_timestamps(traj, op, ot)
        rows.append([LineString(ctraj), cts, r.start_stamp, r.end_stamp])
    else:
        for line in r.POLYLINE:
            traj = list(line.coords)
            if len(traj) < 5:
                continue
            ctraj, cts = correct_timestamps(traj, op, ot)
            rows.append([LineString(ctraj), cts, r.start_stamp, r.end_stamp])

df = pd.DataFrame(rows, columns=["POLYLINE", "timestamp", "start_stamp", "end_stamp"])

# i

21223it [00:23, 892.52it/s] 


In [8]:
df

POLYLINE  \
0      LINESTRING (9.7385 52.3675, 9.742633 52.368053...   
1      LINESTRING (9.7867 52.373, 9.786759 52.373085,...   
2      LINESTRING (9.7781 52.3748, 9.779622 52.377715...   
3      LINESTRING (9.787557 52.391089, 9.786291 52.38...   
4      LINESTRING (9.779924 52.371383, 9.780942 52.37...   
...                                                  ...   
28650  LINESTRING (9.787914 52.390862, 9.787083 52.38...   
28651  LINESTRING (9.787635 52.3908, 9.786406 52.3893...   
28652  LINESTRING (9.72248 52.378239, 9.72678 52.3754...   
28653  LINESTRING (9.781236 52.364432, 9.78042 52.365...   
28654  LINESTRING (9.7686 52.376, 9.768375 52.376103,...   

                                               timestamp  start_stamp  \
0                 [0, 115, 205, 295, 385, 475, 565, 655]   1569071883   
1      [0, 15, 90, 92, 97, 103, 135, 165, 180, 195, 2...   1566574550   
2                                [0, 15, 30, 45, 60, 75]   1567163528   
3                  [0, 15, 31, 45, 60, 75, 90, 105, 120]   1572951667   
4                                            [0, 15, 30]   1572951667   
...                                                  ...          ...   
28650  [0, 6, 10, 11, 16, 21, 25, 26, 32, 35, 40, 45,...   1569062275   
28651         [0, 15, 30, 46, 60, 76, 91, 106, 120, 135]   1568776466   
28652               [0, 30, 60, 122, 152, 182, 212, 242]   1573410514   
28653  [0, 5, 10, 15, 20, 25, 30, 40, 45, 49, 54, 60,...   1573662945   
28654  [0, 2, 3, 54, 74, 89, 103, 119, 122, 128, 134,...   1567093909   

        end_stamp  
0      1569079309  
1      1566583944  
2      1567169273  
3      1572959827  
4      1572959827  
...           ...  
28650  1569075970  
28651  1568790746  
28652  1573424938  
28653  1573677039  
28654  1567105126  

[28655 rows x 4 columns]

In [9]:
df["id"] = np.arange(1, df.shape[0]+1)
df["timestamp"] = df["timestamp"].astype(str)
df["timestamp"] = df["timestamp"].str.replace("[", "")
df["timestamp"] = df["timestamp"].str.replace("]", "")
#df_clipped["timestamp"] = df_clipped["timestamp"].str.replace("  ", ", ")
df.to_csv("../datasets/trajectories/hanover/temporal/mapped_id_poly_clipped_small_graph.csv", sep=";", index=False)

In [10]:
df = pd.read_csv("../datasets/trajectories/hanover/temporal/mapped_id_poly_clipped_small_graph.csv", sep=";")
df

POLYLINE  \
0      LINESTRING (9.7385 52.3675, 9.742633 52.368053...   
1      LINESTRING (9.7867 52.373, 9.786759 52.373085,...   
2      LINESTRING (9.7781 52.3748, 9.779622 52.377715...   
3      LINESTRING (9.787557 52.391089, 9.786291 52.38...   
4      LINESTRING (9.779924 52.371383, 9.780942 52.37...   
...                                                  ...   
28650  LINESTRING (9.787914 52.390862, 9.787083 52.38...   
28651  LINESTRING (9.787635 52.3908, 9.786406 52.3893...   
28652  LINESTRING (9.72248 52.378239, 9.72678 52.3754...   
28653  LINESTRING (9.781236 52.364432, 9.78042 52.365...   
28654  LINESTRING (9.7686 52.376, 9.768375 52.376103,...   

                                               timestamp  start_stamp  \
0                   0, 115, 205, 295, 385, 475, 565, 655   1569071883   
1      0, 15, 90, 92, 97, 103, 135, 165, 180, 195, 21...   1566574550   
2                                  0, 15, 30, 45, 60, 75   1567163528   
3                    0, 15, 31, 45, 60, 75, 90, 105, 120   1572951667   
4                                              0, 15, 30   1572951667   
...                                                  ...          ...   
28650  0, 6, 10, 11, 16, 21, 25, 26, 32, 35, 40, 45, ...   1569062275   
28651           0, 15, 30, 46, 60, 76, 91, 106, 120, 135   1568776466   
28652                 0, 30, 60, 122, 152, 182, 212, 242   1573410514   
28653  0, 5, 10, 15, 20, 25, 30, 40, 45, 49, 54, 60, ...   1573662945   
28654  0, 2, 3, 54, 74, 89, 103, 119, 122, 128, 134, ...   1567093909   

        end_stamp     id  
0      1569079309      1  
1      1566583944      2  
2      1567169273      3  
3      1572959827      4  
4      1572959827      5  
...           ...    ...  
28650  1569075970  28651  
28651  1568790746  28652  
28652  1573424938  28653  
28653  1573677039  28654  
28654  1567105126  28655  

[28655 rows x 5 columns]

In [ ]:
""" 
Speed data analysis
"""

In [14]:
temporal = pd.read_csv("../datasets/trajectories/hanover/temporal/hannover_traffic.csv")

In [22]:
network.gdf_edges.rename(columns={"speed_limi": "speed_limit", "highway_en": "highway_enc"}, inplace=True)

In [23]:
network.gdf_edges

Unnamed_ 0                                 gm_id      id  \
u     v     key                                                             
87037 93516 0          7627  087c80ab-a270-0b4f-417f-7c08f1a24f0b  145195   
15090 8141  0          1327  087c7fd0-a698-0b4f-a183-7c082da54f0b  113275   
14807 87037 0          1295  087c8386-a21e-0b4f-ab80-7c0870a24f0b   88966   
84375 42388 0          7378  087c82c6-7171-0b4f-fe82-7c08ed714f0b  103616   
42388 84375 0          3678  087c82fe-71ed-0b4f-c682-7c0871714f0b  152482   
...                     ...                                   ...     ...   
70598 35872 0          6259  087cb9e9-ede3-0b4e-79ba-7c0888f04e0b  138998   
35872 70598 0          3139  087cba79-f088-0b4e-e9b9-7c08e3ed4e0b  101489   
23242 23243 0          2031  087cba26-e65f-0b4e-9dba-7c08f8e54e0b   12910   
65885 86082 0          5802  087cbd2b-e315-0b4e-25ba-7c08d3e54e0b  118748   
23243 75550 0          2032  087cba9d-e5f8-0b4e-34be-7c08c3e24e0b  168947   

                  fid  speed_limit  \
u     v     key                      
87037 93516 0       0         70.0   
15090 8141  0       1         70.0   
14807 87037 0       2         70.0   
84375 42388 0       3         50.0   
42388 84375 0       4         50.0   
...               ...          ...   
70598 35872 0    1361         50.0   
35872 70598 0    1362         50.0   
23242 23243 0    1363         50.0   
65885 86082 0    1364         50.0   
23243 75550 0    1365         50.0   

                                                            coords  \
u     v     key                                                      
87037 93516 0    [(9.768303900000001, 52.3771314), (9.7683449, ...   
15090 8141  0    [(9.769368, 52.3769124), (9.7693426, 52.376976...   
14807 87037 0    [(9.768221500000001, 52.377861900000006), (9.7...   
84375 42388 0    [(9.755761300000001, 52.37767), (9.75588470000...   
42388 84375 0    [(9.755884700000001, 52.3777258), (9.755761300...   
...                                                            ...   
70598 35872 0    [(9.722083000000001, 52.3917851), (9.722583700...   
35872 70598 0    [(9.7227599, 52.391929100000006), (9.7226905, ...   
23242 23243 0    [(9.7201593, 52.3918455), (9.720055700000001, ...   
65885 86082 0     [(9.719317, 52.3926187), (9.720019, 52.3918453)]   
23243 75550 0    [(9.720055700000001, 52.3919646), (9.719745900...   

                     length  \
u     v     key               
87037 93516 0     41.274658   
15090 8141  0    111.691132   
14807 87037 0     83.502800   
84375 42388 0     10.424039   
42388 84375 0     10.424039   
...                     ...   
70598 35872 0     48.909206   
35872 70598 0     48.909206   
23242 23243 0     14.993560   
65885 86082 0     98.309891   
23243 75550 0    116.397346   

                                                           osm_ids    highway  \
u     v     key                                                                 
87037 93516 0                    '{2696835589,551501215,25753559}'   tertiary   
15090 8141  0    '{25753561,1022695779,551501355,260557584,1022...   tertiary   
14807 87037 0       '{3584276959,2628669590,551501213,2696835589}'   tertiary   
84375 42388 0                              '{654072236,148181777}'   tertiary   
42388 84375 0                              '{148181777,654072236}'   tertiary   
...                                                            ...        ...   
70598 35872 0      '{1619565065,1678001655,6340847835,1226798305}'  secondary   
35872 70598 0      '{1226798305,6340847835,1678001655,1619565065}'  secondary   
23242 23243 0                             '{1484622525,628872258}'  secondary   
65885 86082 0                            '{6221488101,6221488100}'  secondary   
23243 75550 0                      '{628872258,61094001,80191376}'  secondary   

                 highway_enc  \
u     v     key                
87037 93516 0              6   
15090 8141  0              6   
14807 87037 0          

In [24]:
# General temporal data (Note: Nodes are ordered by line graph)
temporal["time"] = pd.to_datetime(temporal["time"])
max_steps, min_steps = temporal["time"].max(), temporal["time"].min()
pad = 0
data = []
for i, index in tqdm(enumerate(network.line_graph.nodes)):
    row = network.gdf_edges.loc[index]
    temp = temporal[temporal["id"]==row["id"]][["time", "speed"]].sort_values("time")
    temp = temp.set_index('time')
    if min_steps not in temp.index:
        temp.loc[min_steps] = pad
    if max_steps not in temp.index:
        temp.loc[max_steps] = pad
    temp = temp.asfreq('15Min', fill_value=0)
    temp[["length", "speed_limit", "highway_enc"]] = row[["length", "speed_limit", "highway_enc"]]
    data.append(temp.values)

1366it [02:28,  9.19it/s]


In [25]:
x = torch.Tensor(data)
x.shape

torch.Size([1366, 5952, 4])

In [26]:
x.isnan().sum()

tensor(0)

In [27]:
torch.save(x, 'temporal_data_small.pt')

In [19]:
# map trajectories to network
from ast import literal_eval


df = pd.read_csv("../datasets/trajectories/hanover/mapped_id_poly_clipped.csv", sep=";")
df["timestamp"] = df["timestamp"].apply(literal_eval)
df["POLYLINE"] = df["POLYLINE"].apply(wkt.loads)

In [10]:
network.fmm_trajectorie_mapping(
    network_file="../osm_data/hanover_temp/edges.shp",
    input_file="../datasets/trajectories/hanover/mapped_id_poly_clipped.csv",
    output_file="../datasets/trajectories/hanover/temporal/road-segment-mapping.txt",
    source_field="u",
    target_field="v"
)

gps file : ../datasets/trajectories/hanover/mapped_id_poly_clipped.csv
id column : id
geom column : POLYLINE
timestamp column : timestamp
x column : x
y column : y
GPS point : false

Result file : ../datasets/trajectories/hanover/temporal/road-segment-mapping.txt
Output fields: opath pgeom spdist cpath mgeom duration speed 
Status: success
Time takes 1252.21 seconds
Total points 4607172 matched 3429926
Map match speed 2739.09 points/s 

[2022-09-15 22:16:53.874] [info] [network.cpp:72] Read network from file ../osm_data/hanover_temp/edges.shp
[2022-09-15 22:16:53.926] [warning] [network.cpp:124] SRID is not found, set to 4326 by default
[2022-09-15 22:16:53.952] [info] [network.cpp:170] Number of edges 8620 nodes 5409
[2022-09-15 22:16:53.952] [info] [network.cpp:171] Field index: id 12 source 0 target 1
[2022-09-15 22:16:53.956] [info] [network.cpp:174] Read network done.
[2022-09-15 22:16:53.956] [info] [network_graph.cpp:17] Construct graph from network edges start
[2022-09-15 22:16

In [11]:
# preprocess the mapping especially the speed and distance values need to be verified
df = pd.read_csv("../datasets/trajectories/hanover/temporal/road-segment-mapping.csv", sep=";")
df_prep = remove_outlier_trajectories(df.copy(), min_edges_traversed=3, max_speed=0.000251)
df_prep.to_csv("../datasets/trajectories/hanover/temporal/road_segment_map_final.csv", sep=";")

Pandas Apply:   0%|          | 0/109207 [00:00<?, ?it/s]

Pandas Apply:   0%|          | 0/109207 [00:00<?, ?it/s]

/home/paul/repos/Road-Network-Embedding-Generator/generator/preprocess.py:106: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df[(df["speed_mean"] > max_speed)]["speed"] = df[(df["speed_mean"] > max_speed)][


Pandas Apply:   0%|          | 0/85984 [00:00<?, ?it/s]

/home/paul/repos/Road-Network-Embedding-Generator/generator/preprocess.py:109: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df["speed_mean"] = df["speed"].swifter.apply(np.mean)


In [8]:
df_prep = pd.read_csv("../datasets/trajectories/hanover/temporal/road_segment_map_final.csv", sep=";")

In [14]:
d = df[df["id"]==1872]
print(d)
print(d["end_stamp"] - d["start_stamp"])
print(d["POLYLINE"].values)

                                              timestamp  start_stamp  \
1871     0    2    5   10   14   16   17   24   27  ...   1574998674   

       end_stamp                                           POLYLINE    id  
1871  1575001061  LINESTRING (9.630023942886398 52.4212434865260...  1872  
1871    2387
dtype: int64
['LINESTRING (9.630023942886398 52.421243486526095, 9.629115 52.421171, 9.628161 52.421147, 9.627631 52.421338, 9.627528 52.421801, 9.627596 52.422034, 9.628007 52.422238, 9.62872 52.422043, 9.630023942886398 52.421243486526095)']


In [16]:
df_prep[df_prep["id"]==1872]

Unnamed: 0    id                                         opath  \
1         226  1872  4688,4688,6882,6882,6882,6882,6882,6882,5570   

                                              spdist  \
1  0.000911354,0.000955415,0.00056174,0.000469219...   

                                               pgeom  \
1  LINESTRING(9.63002577495 52.4212081598,9.62911...   

                      cpath  \
1  (4688, 6882, 8047, 5570)   

                                               mgeom duration  \
1  LINESTRING(9.63002577495 52.4212081598,9.62947...    15,30   

                                   speed  speed_mean  
1  [6.0756949851e-05, 3.18471622339e-05]    0.000046